In [23]:
import math 
import re
import itertools

import numpy as np
import pandas as pd
from IPython.display import display, HTML

import sqlite3
import json

In [24]:
# Utility Functions and Classes
def digit_cnt(n):
    if n > 0:
        return int(math.log10(n))+1
    elif n == 0:
        return 1
    elif n < 0:
        return int(math.log10(-n))+2
    

In [25]:
con = sqlite3.connect("/home/skye/Documents/Scripts/FRC/2022/scouting/cblite/wildrank.cblite2/db.sqlite3")

In [26]:
cursor = con.cursor()

In [27]:
cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
print(cursor.fetchall())

[('docs',), ('revs',), ('sqlite_sequence',), ('localdocs',), ('views',), ('info',), ('maps_1',), ('sqlite_stat1',)]


In [31]:
# TBA Retrieved Data
cursor.execute("SELECT json FROM revs where doc_type = 'match' AND doc_id=1")
col_names = list(map(lambda x: x[0], cursor.description))
print(col_names)
print(cursor.fetchall())

df_tba_results = pd.read_sql_query("SELECT json FROM revs where doc_type = 'match'", con)
df_tba_results_e = df_tba_results.join(df_tba_results['json'].apply(json.loads).apply(pd.Series))
df_tba_results_e = df_tba_results_e.sort_values(by=['time'],ignore_index=True).reset_index(drop=True)
#df_tba_results_alliances = pd.DataFrame.from_dict(df_tba_results_e['alliances'])
df_tba_results_alliances = pd.concat({k: pd.DataFrame(v).T for k, v in df_tba_results_e['alliances'].items()}, axis=0)
df_tba_results_alliances = pd.DataFrame(df_tba_results_alliances['team_keys'])

df_tba_results_alliances[['team1','team2','team3']] = pd.DataFrame(df_tba_results_alliances['team_keys'].tolist(), index= df_tba_results_alliances.index)
all_teams = pd.unique(df_tba_results_alliances[['team1','team2','team3']].values.ravel('K'))
#display(HTML(df_tba_results_alliances.to_html()))
#print(all_teams)

team_matches = {}
for team in all_teams:
    select_indices = list(np.where((df_tba_results_alliances["team1"] == team) | \
                                   (df_tba_results_alliances["team2"] == team) | \
                                   (df_tba_results_alliances["team3"] == team))[0])
    #select_indices = [l%2 for l in select_indices]
    team_matches[team] = select_indices
    

#print(pd.DataFrame(team_matches).T)
df_alliance_color = pd.DataFrame(team_matches).T
#df_alliance_color.replace({0: 'red', 1: 'blue'}, inplace=True) 
#display(HTML(df_alliance_color.to_html()))

['json']
[]
10
10
10
10
10
10
10
10
11
10
10
10
10
10
10
10
11
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10


ValueError: All arrays must be of the same length

In [7]:
# Get our data
cursor.execute("SELECT json FROM revs where doc_type = 'match_result'")
df_user_results = pd.read_sql_query("SELECT json FROM revs where doc_type = 'match_result'", con)
col_names = list(map(lambda x: x[0], cursor.description))
results = cursor.fetchall()
print(col_names)
pd.options.display.max_colwidth =10000

df_user_results.head(60)



['json']


json
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  b'{"match_key":"2022misjo_qm10","data":{"auto-robot_contact":false,"post_match-floor_pickup_rating":"2","auto-score_cargo_low":0,"cycles":[{"missed_shot":true,"defended_shot":false,"location_1":false,"hub_upper_score":true,"location_8":false,"location_6":false,"location_7":false,"location_4":false,"location_5":false,"hub_lower_score":false,"location_2":false,"location_3":true},{"missed_shot":true,"defended_shot":false,"location_1":false,"hub_upper_score":true,"location_8":false,"location_6":false,"location_7":false,"location_4":true,"location_5":false,"hub_lower_score":false,"location_2":false,"location_3":false},{"missed_shot":true,"defended_shot":false,"location_1":false,"hub_upper_score":true,"location_8":false,"location_6":false,"location_7":false,"location_4":true,"location_5":false,"hub_lower_score":false,"location_2":false,"location_3":false},{"missed_shot":false,"defended_shot":false,"location_1":false,"hub_upper_score":true,"location_8":false,"location_6":false,"location_7":false,"location_4":true,"location_5":false,"hub_lower_score":false,"location_2":false,"location_3":false},{"missed_shot":false,"defended_shot":false,"location_1":false,"hub_upper_score":true,"location_8":false,"location_6":false,"location_7":false,"location_4":false,"location_5":false,"hub_lower_score":false,"location_2":false,"location_3":true},{"missed_shot":false,"defended_shot":false,"location_1":false,"hub_upper_score":true,"location_8":false,"location_6":false,"location_7":false,"location_4":false,"location_5":false,"hub_lower_score":false,"location_2":false,"location_3":true}],"auto-startLoc":"1","post_match-climb_level":"2","post_match-tipped":false,"post_match-robot_speed":"0","auto-score_cargo_high":1,"auto-drive":true,"auto-miss_cargo_low":0,"post_match-excessive_fouls":false,"auto-miss_cargo_high":0,"post_match-climb_time":"About 10sec"},"type":"match_result","team_key":"frc216","users":["2767"]}'
1                                                                                                                                      

In [8]:
# convert our column of json data to a df with all variables from that json
df_user_results_e = df_user_results.join(df_user_results['json'].apply(json.loads).apply(pd.Series))

In [9]:
goal_to_analyze = 1 #0 = unknown, 1 = high, 2=low
color_right_side_app_UI = "blue"        #"red" or "blue" 



#create a filter if we want to exclude any teams from our global stats to prevent dilution
teams_with_data = df_user_results_e['team_key'].unique()
teams_to_exclude = ['frc000']
teams_to_include = [x for x in teams_with_data if x not in teams_to_exclude]
print(f'Teams used for calculation of averages: {teams_to_include}\n----')
df_user_results_teams = df_user_results_e[df_user_results_e['team_key'].isin(teams_to_include)]


## columns we will use
loc_col_list = ['location_1', 'location_2', 'location_3', 'location_4', 'location_5',
                       'location_6', 'location_7', 'location_8']
cycle_col_list = ['hub_upper_score','hub_lower_score','missed_shot', 'defended_shot',
                       'location_1', 'location_2', 'location_3', 'location_4', 'location_5',
                       'location_6', 'location_7', 'location_8']

match_col_list = ['post_match-robot_speed', 'post_match-climb_time', 'post_match-floor_pickup_rating',
                  'auto-startLoc','auto-score_cargo_high', 'auto-score_cargo_low','auto-drive',
                  'post_match-tipped', 'auto-miss_cargo_high', 'auto-miss_cargo_low','auto-robot_contact',
                  'post_match-climb_level']
additional_match_col_list = ['alliance_color', 'hub_unknown_scored', 'hub_upper_scored', 'hub_lower_scored',
                            'hub_unknown_missed', 'hub_upper_missed', 'hub_lower_missed']


#Grab stats for all locations from teams querried
all_cycle_locs = pd.DataFrame()
all_match_info = pd.DataFrame()
for idx, d in df_user_results_teams.iterrows():
    match = int(''.join(map(str,re.findall('^.*qm([0-9]+)$',d['match_key'])))) #strip the match number from the end of the match key, the only gaurentee we have is the matches are orginized by the left most digit, easier to just snag the match number and link it to an alliance color 
    team = d['team_key']
    df_tba_match = df_tba_results_alliances.loc[match-1]    #fix out 1 indexed match keys to 0 indexed match data frame
    alliance_color = df_tba_match.loc[(df_tba_match['team1'] == team) | \
                                  (df_tba_match['team2'] == team) | \
                                  (df_tba_match['team3'] == team)].index[0]
  
    m = d['data']
    df_match = pd.DataFrame(m)
    print(type(d['data']))
    if ('cycles' in m) == False :
        print(f"No cycles to parse!")
        continue
    
    df_cycles = pd.DataFrame(m['cycles'])
    if df_cycles.empty:                                               # we need to contitnue and jump this iteration of the for loop if there are no cycles
        print(f"No cycles to parse!")
        continue
    #cycle_col_list = list(df_cycles.columns)
    print('Type', type(df_cycles.columns.values.tolist()))
    print('Type', type(match_col_list[0]))
    df_cycles.replace({False: 0, True: 1}, inplace=True)                # cast boolean values across all columns to int

    #df_cycles = df_cycles[cycle_col_list]                               # TODO df_cycles is out of order without this line, hard to read
    print(df_cycles.info())
    df_match['team_key'] = team[3:]
    df_cycles['team_key'] = team[3:]
    df_match['match_idx'] = str(match)
    df_cycles['match_idx'] = str(match)
    
    
    
    df_cycles['loc'] = df_cycles.loc[:, loc_col_list[::-1]].astype(str).sum(axis=1).astype(int).apply(digit_cnt)  # we invert the list w/ [::-1] because we want 1 to be on the left, not 8
    df_cycles['loc_checksum'] = df_cycles[loc_col_list].sum(axis=1)
    df_cycles.loc[df_cycles['loc_checksum'] != 1, 'loc'] = 0
    
    df_cycles['target_goal'] = df_cycles[cycle_col_list[:2][::-1]].astype(str).sum(axis=1).astype(int).apply(digit_cnt) #0 is unknown, 1 is upper hub goal, 2 is lower hub goal
    df_cycles['target_checksum'] = df_cycles[loc_col_list].sum(axis=1)
    df_cycles.loc[df_cycles['target_checksum'] != 1, 'target_goal'] = 0
    
    
    loc_swap_dict = {1:4 , 2:3 , 3:2 , 4:1 , 5:8 , 6:7 , 7:6 , 8:5 }  # alignment mapping of locs to rotate 180deg
    if alliance_color == color_right_side_app_UI:
        df_cycles.replace({"loc":loc_swap_dict}, inplace=True)  
    
    
    all_cycle_locs = all_cycle_locs.append(df_cycles[['team_key', 'match_idx' ,'loc','target_goal','missed_shot','defended_shot']])
    df_match['alliance_color'] = alliance_color
    df_match['hub_unknown_scored'] = ((df_cycles['target_goal'] == 0)&(df_cycles['missed_shot'] == 0)).sum()
    df_match['hub_upper_scored'] = ((df_cycles['target_goal'] == 1)&(df_cycles['missed_shot'] == 0)).sum()
    df_match['hub_lower_scored'] = ((df_cycles['target_goal'] == 2)&(df_cycles['missed_shot'] == 0)).sum()
    df_match['hub_unknown_missed'] = ((df_cycles['target_goal'] == 0)&(df_cycles['missed_shot'] == 1)).sum()
    df_match['hub_upper_missed'] = ((df_cycles['target_goal'] == 1)&(df_cycles['missed_shot'] == 1)).sum()
    df_match['hub_lower_missed'] = ((df_cycles['target_goal'] == 2)&(df_cycles['missed_shot'] == 1)).sum()
    
    _match_col_list_tmp = list(itertools.chain(['team_key', 'match_idx'], additional_match_col_list, match_col_list))    #list of cols of non cycle match vars to sent to df that will be ultimatly parsed to json
    df_match_to_all = df_match[_match_col_list_tmp]
    all_match_info = all_match_info.append(df_match_to_all.iloc[:1], ignore_index=True) # we extract a range of [:1] because assigning a single row dataframe (when extracted as .iloc[0]) is viewed as a series, which messes up dtypes
#display(HTML(all_cycle_locs.to_html()))
display(HTML(all_match_info.to_html()))
    

Teams used for calculation of averages: ['frc216', 'frc244', 'frc5056', 'frc5535', 'frc74', 'frc904', 'frc1254', 'frc1940', 'frc226', 'frc288', 'frc2959', 'frc6128', 'frc2054', 'frc4003', 'frc5110', 'frc5182', 'frc5927', 'frc7195', 'frc4325', 'frc5610', 'frc5980', 'frc7210', 'frc7814', 'frc3452', 'frc3688', 'frc910', 'frc4237', 'frc6114', 'frc2767', 'frc3620', 'frc6588']
----
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6 entries, 0 to 5
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   missed_shot      6 non-null      int64
 1   defended_shot    6 non-null      int64
 2   location_1       6 non-null      int64
 3   hub_upper_score  6 non-null      int64
 4   location_8       6 non-null      int64
 5   location_6       6 non-null      int64
 6   location_7       6 non-null      int64
 7   location_4       6 non-null      int64
 8   location_5       6 no

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14 entries, 0 to 13
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   missed_shot      14 non-null     int64
 1   defended_shot    14 non-null     int64
 2   location_1       14 non-null     int64
 3   hub_upper_score  14 non-null     int64
 4   location_8       14 non-null     int64
 5   location_6       14 non-null     int64
 6   location_7       14 non-null     int64
 7   location_4       14 non-null     int64
 8   location_5       14 non-null     int64
 9   hub_lower_score  14 non-null     int64
 10  location_2       14 non-null     int64
 11  location_3       14 non-null     int64
dtypes: int64(12)
memory usage: 1.4 KB
None
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6 entries, 0 to 5
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  

<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14 entries, 0 to 13
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   missed_shot      14 non-null     int64
 1   defended_shot    14 non-null     int64
 2   location_1       14 non-null     int64
 3   hub_upper_score  14 non-null     int64
 4   location_8       14 non-null     int64
 5   location_6       14 non-null     int64
 6   location_7       14 non-null     int64
 7   location_4       14 non-null     int64
 8   location_5       14 non-null     int64
 9   hub_lower_score  14 non-null     int64
 10  location_2       14 non-null     int64
 11  location_3       14 non-null     int64
dtypes: int64(12)
memory usage: 1.4 KB
None
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7 entries, 0 to 6
Data columns (total 12 columns):
 #   Column           Non-Nu

<class 'dict'>
No cycles to parse!
<class 'dict'>
No cycles to parse!
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10 entries, 0 to 9
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   missed_shot      10 non-null     int64
 1   defended_shot    10 non-null     int64
 2   location_1       10 non-null     int64
 3   hub_upper_score  10 non-null     int64
 4   location_8       10 non-null     int64
 5   location_6       10 non-null     int64
 6   location_7       10 non-null     int64
 7   location_4       10 non-null     int64
 8   location_5       10 non-null     int64
 9   hub_lower_score  10 non-null     int64
 10  location_2       10 non-null     int64
 11  location_3       10 non-null     int64
dtypes: int64(12)
memory usage: 1.1 KB
None
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5 entries,

<class 'dict'>
No cycles to parse!
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9 entries, 0 to 8
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   missed_shot      9 non-null      int64
 1   defended_shot    9 non-null      int64
 2   location_1       9 non-null      int64
 3   hub_upper_score  9 non-null      int64
 4   location_8       9 non-null      int64
 5   location_6       9 non-null      int64
 6   location_7       9 non-null      int64
 7   location_4       9 non-null      int64
 8   location_5       9 non-null      int64
 9   hub_lower_score  9 non-null      int64
 10  location_2       9 non-null      int64
 11  location_3       9 non-null      int64
dtypes: int64(12)
memory usage: 992.0 bytes
None
<class 'dict'>
No cycles to parse!
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5 entr

...

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5 entries, 0 to 4
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   missed_shot      5 non-null      int64
 1   defended_shot    5 non-null      int64
 2   location_1       5 non-null      int64
 3   hub_upper_score  5 non-null      int64
 4   location_8       5 non-null      int64
 5   location_6       5 non-null      int64
 6   location_7       5 non-null      int64
 7   location_4       5 non-null      int64
 8   location_5       5 non-null      int64
 9   hub_lower_score  5 non-null      int64
 10  location_2       5 non-null      int64
 11  location_3       5 non-null      int64
dtypes: int64(12)
memory usage: 608.0 bytes
None
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8 entries, 0 to 7
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           -------------

<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7 entries, 0 to 6
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   missed_shot      7 non-null      int64
 1   defended_shot    7 non-null      int64
 2   location_1       7 non-null      int64
 3   hub_upper_score  7 non-null      int64
 4   location_8       7 non-null      int64
 5   location_6       7 non-null      int64
 6   location_7       7 non-null      int64
 7   location_4       7 non-null      int64
 8   location_5       7 non-null      int64
 9   hub_lower_score  7 non-null      int64
 10  location_2       7 non-null      int64
 11  location_3       7 non-null      int64
dtypes: int64(12)
memory usage: 800.0 bytes
None
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2 entries, 0 to 1
Data columns (total 12 columns):
 #   Column           Non

<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2 entries, 0 to 1
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   missed_shot      2 non-null      int64
 1   defended_shot    2 non-null      int64
 2   location_1       2 non-null      int64
 3   hub_upper_score  2 non-null      int64
 4   location_8       2 non-null      int64
 5   location_6       2 non-null      int64
 6   location_7       2 non-null      int64
 7   location_4       2 non-null      int64
 8   location_5       2 non-null      int64
 9   hub_lower_score  2 non-null      int64
 10  location_2       2 non-null      int64
 11  location_3       2 non-null      int64
dtypes: int64(12)
memory usage: 320.0 bytes
None
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10 entries, 0 to 9
Data columns (total 12 columns):
 #   Column           No

<class 'dict'>
No cycles to parse!
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1 entries, 0 to 0
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   missed_shot      1 non-null      int64
 1   defended_shot    1 non-null      int64
 2   location_1       1 non-null      int64
 3   hub_upper_score  1 non-null      int64
 4   location_8       1 non-null      int64
 5   location_6       1 non-null      int64
 6   location_7       1 non-null      int64
 7   location_4       1 non-null      int64
 8   location_5       1 non-null      int64
 9   hub_lower_score  1 non-null      int64
 10  location_2       1 non-null      int64
 11  location_3       1 non-null      int64
dtypes: int64(12)
memory usage: 224.0 bytes
None
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11 entries, 0 to 10
Data columns (total 1

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13 entries, 0 to 12
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   missed_shot      13 non-null     int64
 1   defended_shot    13 non-null     int64
 2   location_1       13 non-null     int64
 3   hub_upper_score  13 non-null     int64
 4   location_8       13 non-null     int64
 5   location_6       13 non-null     int64
 6   location_7       13 non-null     int64
 7   location_4       13 non-null     int64
 8   location_5       13 non-null     int64
 9   hub_lower_score  13 non-null     int64
 10  location_2       13 non-null     int64
 11  location_3       13 non-null     int64
dtypes: int64(12)
memory usage: 1.3 KB
None
<class 'dict'>
Type <class 'list'>
Type <class 'str'>
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7 entries, 0 to 6
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  

In [10]:
#generate a dummy col for every possible location target miss and defense combination
loc_range = list(range(0,9,1))
target_range = list(range(0,3,1))
missed_range = [0,1]
defense_range = [0,1]
team_dummy = "0000"
match_idx_dummy = "0"
cycles_dummy = pd.DataFrame(itertools.product(loc_range, target_range, missed_range, defense_range),
                            columns=['loc', 'target_goal', 'missed_shot', 'defended_shot'])
cycles_dummy['team_key'] = team_dummy
cycles_dummy['match_idx'] = match_idx_dummy

agg_cycles = all_cycle_locs
agg_cycles = pd.concat([agg_cycles, cycles_dummy], axis=0, ignore_index=True)
#display(HTML(agg_cycles.sort_values(by=['team_key', 'match_idx']).to_html()))

agg_cycles['tgt-loc-miss-def'] = (agg_cycles['target_goal']).astype(str) \
                                + (agg_cycles['loc']).astype(str) \
                                + (agg_cycles['missed_shot']).astype(str) \
                                + (agg_cycles['defended_shot']).astype(str)

agg_cycles = pd.get_dummies(agg_cycles, prefix=['tgt-loc-miss-def'], columns=["tgt-loc-miss-def"])
agg_cycles.drop(['loc', 'target_goal', 'missed_shot', 'defended_shot'], axis=1, inplace=True)
agg_cycles_col_names = agg_cycles.columns
agg_cycles = agg_cycles.groupby(['team_key', 'match_idx'],as_index=False)[agg_cycles_col_names[2:]].sum()


# <--- 
agg_cycles_col_names = agg_cycles.columns

hub_scored_upper_clean = agg_cycles.groupby(['team_key', 'match_idx'])[agg_cycles_col_names[42:71:4]].sum()
hub_scored_lower_clean = agg_cycles.groupby(['team_key', 'match_idx'])[agg_cycles_col_names[78:116:4]].sum()
hub_missed_upper_clean = agg_cycles.groupby(['team_key', 'match_idx'])[agg_cycles_col_names[44:73:4]].sum()
hub_missed_lower_clean = agg_cycles.groupby(['team_key', 'match_idx'])[agg_cycles_col_names[80:118:4]].sum()

hub_scored_upper_def = agg_cycles.groupby(['team_key', 'match_idx'])[agg_cycles_col_names[43:72:4]].sum()
hub_scored_lower_def = agg_cycles.groupby(['team_key', 'match_idx'])[agg_cycles_col_names[79:117:4]].sum()
hub_missed_upper_def = agg_cycles.groupby(['team_key', 'match_idx'])[agg_cycles_col_names[45:74:4]].sum()
hub_missed_lower_def = agg_cycles.groupby(['team_key', 'match_idx'])[agg_cycles_col_names[81:119:4]].sum()

shots_clean = pd.DataFrame()
shots_def = pd.DataFrame()
shots_all = pd.DataFrame()
for loc in range(1,9): 
    df_clean = pd.DataFrame({'location_clean': loc,
                                'hub_scored_upper_clean':hub_scored_upper_clean.iloc[:,loc-1],
                                'hub_scored_lower_clean':hub_scored_lower_clean.iloc[:,loc-1],
                                'hub_missed_upper_clean':hub_missed_upper_clean.iloc[:,loc-1],
                                'hub_missed_lower_clean':hub_missed_lower_clean.iloc[:,loc-1]})
    shots_clean[f'shots_clean{loc}'] = df_clean.apply(pd.Series.to_dict, axis=1)
    
    df_def = pd.DataFrame({'location_def': loc,
                                'hub_scored_upper_def':hub_scored_upper_def.iloc[:,loc-1],
                                'hub_scored_lower_def':hub_scored_lower_def.iloc[:,loc-1],
                                'hub_missed_upper_def':hub_missed_upper_def.iloc[:,loc-1],
                                'hub_missed_lower_def':hub_missed_lower_def.iloc[:,loc-1]})
    shots_def[f'shots_def{loc}'] = df_def.apply(pd.Series.to_dict, axis=1)
    
    df_all = pd.merge(df_clean, df_def, how='left', left_on=['team_key','match_idx'], right_on = ['team_key','match_idx'])
    df_all['location_all'] = df_all['location_clean']
    df_all['hub_scored_upper_all'] = df_all['hub_scored_upper_clean'] + df_all['hub_scored_upper_def']
    df_all['hub_scored_lower_all'] = df_all['hub_scored_lower_clean'] + df_all['hub_scored_lower_def']
    df_all['hub_missed_upper_all'] = df_all['hub_missed_upper_clean'] + df_all['hub_missed_upper_def']
    df_all['hub_missed_lower_all'] = df_all['hub_missed_lower_clean'] + df_all['hub_missed_lower_def']
    df_all = df_all[['location_all','hub_scored_upper_all', 'hub_scored_lower_all','hub_missed_upper_all', 'hub_missed_lower_all']]
    shots_all[f'shots_all{loc}'] = df_all.apply(pd.Series.to_dict, axis=1)
    
print(shots_def.head())
print(shots_all.head())
shots_clean['shots_clean'] = shots_clean.apply(pd.Series.to_list, axis=1)
shots_clean = shots_clean[['shots_clean']].reset_index() 

shots_def['shots_def'] = shots_def.apply(pd.Series.to_list, axis=1)
shots_def = shots_def[['shots_def']].reset_index()

shots_all['shots_all'] = shots_all.apply(pd.Series.to_list, axis=1)
shots_all = shots_all[['shots_all']].reset_index()

# --->

# --- Clean up some climb data stuff
# assumption is: all climb levels will be utilized at some point, or else we need to create some matches with different climb levels for dummy team 0000
all_match_info = pd.concat([all_match_info, pd.get_dummies(all_match_info['post_match-climb_level'], prefix='post_match-climb_level')], axis=1)

# --->

# --- Combine everything to send to json
agg_cycles = pd.merge(agg_cycles, shots_clean, how='left', left_on=['team_key','match_idx'], right_on = ['team_key','match_idx'])
agg_cycles = pd.merge(agg_cycles, shots_def, how='left', left_on=['team_key','match_idx'], right_on = ['team_key','match_idx'])
agg_cycles = pd.merge(agg_cycles, shots_all, how='left', left_on=['team_key','match_idx'], right_on = ['team_key','match_idx'])
agg_cycles = agg_cycles[agg_cycles.columns.drop(list(agg_cycles.filter(regex='tgt-loc-miss-def')))]
agg_cycles = agg_cycles.drop(agg_cycles[(agg_cycles['team_key'] == "0000") & \
                                        (agg_cycles['match_idx'] == "0")].index)
all_match_info['post_match-climb_time'].replace({"!No Climb": 0, "About 05sec or less": 5, "About 10sec":10, "About 15sec":15, \
                                                 "About 20sec":20, "About 25sec":25, "About 30sec +":30, }, inplace=True)

team_matches = pd.merge(all_match_info, agg_cycles,  how='left', left_on=['team_key','match_idx'], right_on = ['team_key','match_idx'])
display(HTML(team_matches.sort_values(by=['team_key', 'match_idx']).to_html()))

                                                                                                                                         shots_def1  \
team_key match_idx                                                                                                                                    
0000     0          {'location_def': 1, 'hub_scored_upper_def': 1, 'hub_scored_lower_def': 1, 'hub_missed_upper_def': 1, 'hub_missed_lower_def': 1}   
1254     11         {'location_def': 1, 'hub_scored_upper_def': 0, 'hub_scored_lower_def': 0, 'hub_missed_upper_def': 0, 'hub_missed_lower_def': 0}   
         14         {'location_def': 1, 'hub_scored_upper_def': 0, 'hub_scored_lower_def': 0, 'hub_missed_upper_def': 0, 'hub_missed_lower_def': 0}   
         25         {'location_def': 1, 'hub_scored_upper_def': 0, 'hub_scored_lower_def': 0, 'hub_missed_upper_def': 0, 'hub_missed_lower_def': 0}   
         29         {'location_def': 1, 'hub_scored_upper_def': 0, 'hub_scored_lower_def': 0, 

In [11]:
result = team_matches.to_json(orient="records")

parsed = json.loads(result)

x = json.dumps(parsed, indent=4) 
x = '{"data":' + x +'}'
print(x)

out_path = "./out.json"
with open(out_path, 'w') as f:
    f.write(x)

{"data":[
    {
        "team_key": "216",
        "match_idx": "10",
        "alliance_color": "blue",
        "hub_unknown_scored": 0,
        "hub_upper_scored": 3,
        "hub_lower_scored": 0,
        "hub_unknown_missed": 0,
        "hub_upper_missed": 3,
        "hub_lower_missed": 0,
        "post_match-robot_speed": "0",
        "post_match-climb_time": 10,
        "post_match-floor_pickup_rating": "2",
        "auto-startLoc": "1",
        "auto-score_cargo_high": 1,
        "auto-score_cargo_low": 0,
        "auto-drive": true,
        "post_match-tipped": false,
        "auto-miss_cargo_high": 0,
        "auto-miss_cargo_low": 0,
        "auto-robot_contact": false,
        "post_match-climb_level": "2",
        "post_match-climb_level_0": 0,
        "post_match-climb_level_1": 0,
        "post_match-climb_level_2": 1,
        "post_match-climb_level_3": 0,
        "post_match-climb_level_4": 0,
        "shots_clean": [
            {
                "location_clean": 1,
  